In [10]:
# parameters
import pickle
import com_func
import pandas as pd

import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

def dummy(doc):
    return doc

threshold = 10
cutoff = 3
Dataset = "pubmed"

combined_emb = "p2v"

In [11]:
def dummy(doc):
    return doc
def read_labeled_file(infile):
    LabeledRecords_original = []
    with open(infile, 'r', encoding = 'utf8') as f:
        for line in f:
            read_data = line.split("\t")
            # get ride of bad formated lines
            if(len(read_data)==13 or len(read_data)==12):
                paper_detail = {"paperID": read_data[0], "authorID":read_data[1]}
                LabeledRecords_original.append(paper_detail)
            else:
                print(len(read_data))
        f.close()
    return pd.DataFrame(LabeledRecords_original)

In [12]:
# read trained rec to rec textual graph
def read_combined_embedding(Dataset = "pubmed", emb_type = "off"):
    textual_emb = []
    while True:
        if emb_type == "p2v":
            loadDir = "../Data/"+Dataset+"/vectors/p2v/extracted_labeled_p2v.txt"
            with open(loadDir, 'r', encoding = 'utf8') as f:
                for line in f:
                    read_data = line.split(" ")
                    paper_Vectors = read_data
                    textual_emb.append(paper_Vectors)
            f.close()

            print("Total textual vector records:",len(textual_emb))
            print(textual_emb[0])
            break
        elif emb_type == "off":
            break
        else:
            print("Embedding type not available, selecting default setting")
            emb_type="pv_dbow"
    return textual_emb

In [13]:
# remove author(positive sample) from other(negative sample)
import random
def extractNegativeSample(positiveSample, allSample):
    negativeSample = [x for x in allSample if x not in positiveSample]
    return negativeSample

In [14]:
def extract_embedding(all_embedding, pid):
    extracted_emb = []
    wanted_pid = pid.values.tolist()
    # only if embedding exist
    if len(all_embedding)>0:
        for paper_embedding in all_embedding:
            if paper_embedding[0] in wanted_pid:
                extracted_emb.append(paper_embedding)
    
    extracted_emb = pd.DataFrame(extracted_emb)
    # only if embedding exist
    if len(all_embedding)>0:
        # reorder embedding with pid and fill empty record with 0
        extracted_emb = pd.merge(pid.to_frame(), extracted_emb, left_on='paperID', right_on=0, how='outer')
        # fill missing value with 0
        extracted_emb.fillna(0, inplace = True)
        # remove index
        extracted_emb.drop(['paperID', 0], axis=1, inplace=True)
    return extracted_emb

In [15]:
from sklearn.model_selection import KFold
from sklearn import metrics
from sklearn.metrics import precision_score, recall_score,f1_score,accuracy_score
# cross validation
def k_fold_cv(data, label, clf, k=10):
    kf = KFold(n_splits=k, shuffle=False)
    allTrueLabel = []
    allPredLabel = []
    for train_index, test_index in kf.split(data):
        # print("TRAIN:", train_index, " \n TEST:", test_index)
        # split train and test
        data_train, data_test = data[train_index], data[test_index]
        label_train, label_test = label[train_index], label[test_index]
        # fit data to clf
        clf.fit(data_train, label_train)
        # get predicted label
        label_pred = clf.predict(data_test)
        allTrueLabel.extend(label_test)
        allPredLabel.extend(label_pred)
        # print("True positive: {tp}, False positive: {fp}, False negative: {fn}, True negative: {tn}"
        # .format(tp=round_tp, fp=round_fp, fn=round_fn, tn=round_tn))

    accuracy = accuracy_score(allTrueLabel, allPredLabel)
    f1 = f1_score(allTrueLabel, allPredLabel,average='macro')
    
    print(metrics.classification_report(allTrueLabel, allPredLabel))
    print(metrics.confusion_matrix(allTrueLabel, allPredLabel).ravel())
    
    return accuracy, f1

In [16]:
# read pretrained embeddings
p2v_embedding = read_combined_embedding(Dataset, combined_emb)
print(len(p2v_embedding))

Total textual vector records: 135768
['8077', '-0.30562', '-0.14224', '-0.295474', '-0.162722', '-0.105769', '0.0561656', '-0.0797713', '-0.0459434', '-0.108158', '0.0544028', '-0.0999472', '-0.0974462', '-0.0508525', '0.151689', '-0.232159', '-0.0359973', '0.0194938', '0.0693435', '-0.112974', '-0.0311077', '0.078018', '-0.0631533', '0.0524421', '0.137697', '0.101945', '-0.0200023', '-0.10946', '0.0944765', '0.00272627', '-0.104189', '-0.0349762', '-0.011765', '0.00508523', '-0.163048', '-0.0154401', '-0.0480973', '0.031805', '-0.0608286', '-0.0115254', '0.0359856', '-0.0689324', '-0.0651454', '0.079306', '-0.0847919', '-0.164983', '-0.172415', '0.0292607', '0.0193611', '-0.0923435', '-0.056113', '0.0077811', '0.0317496', '0.0495394', '-0.139721', '-0.0199847', '-0.0592476', '0.0124314', '0.0360882', '0.134681', '-0.236409', '-0.0483922', '0.0447124', '-0.0540506', '-0.195456', '0.0219141', '0.0426379', '-0.024773', '-0.122287', '0.0582443', '-0.034571', '-0.0649725', '-0.0880582', '0

In [17]:
# load the file
import sys
import io
import os
import collections
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import MultinomialNB
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score


fileDir = "../Data/"+Dataset+"/canopies_labeled/"
listfiles = os.listdir(fileDir)

# fix random seed for reproducibility
np.random.seed(1)

# collect statistic to output
allname = []
positive_sample_size = []
negative_sample_size = []

all_svcLinear_accuracy = []
all_svcLinear_f1 = []
all_LR_accuracy = []
all_LR_f1 = []

# read all file in labeled group
for file in listfiles:
    # group name
    temp = file.split("_")
    name = temp[1]+"_"+temp[-1]
    print("For name: ",name)
    # read needed content in labeled file
    labeled_data = read_labeled_file(fileDir+file)
    # collect all labeled sample
    all_labeled_sample = labeled_data["paperID"].tolist()
    print("total sample size before apply threshold: ",len(labeled_data))
    # count number of paper each author write based on author ID
    paperCounter = collections.Counter(labeled_data["authorID"])
    print(paperCounter)
    # collect per class statistic
    for k in list(paperCounter):
        if paperCounter[k] < threshold:
            del paperCounter[k]
    temp =list(paperCounter.keys())
    print(temp)
    # remove authors that write smaller than threshold number of authors
    temp = labeled_data[labeled_data.authorID.isin(temp)]
    author_list = set(temp["authorID"])
    # if only have one class or no class pass the threshold, not applicable
    if(len(paperCounter)==0) or (len(paperCounter)==1):
        print(name," pass")
    else:
        counter = 0
        # loop through each author have label, one vs rest
        for author in author_list:
            author_name = name+'_'+str(counter)
            counter+=1
            allname.append(author_name)
            mask = labeled_data["authorID"] == author
            temp = labeled_data[mask]
            positive_sample_pid = temp["paperID"].tolist()
            negative_sample_pid = extractNegativeSample(positive_sample_pid, all_labeled_sample)
            # append to statistic collection
            positive_sample_size.append(len(positive_sample_pid))
            negative_sample_size.append(len(negative_sample_pid))
            # form positive and negative (negative class come from similar name group)
            all_authors = []
            all_authors.append(positive_sample_pid)
            all_authors.append(negative_sample_pid)
            appended_data = []
            for label, pid in enumerate(all_authors):
                # create df save one author data 
                authordf = pd.DataFrame({"paperID":pid})
                authordf['label'] = label
                appended_data.append(authordf)
            processed_data = pd.concat(appended_data, axis=0,ignore_index=True)
            # shuffle the data
            processed_data = processed_data.sample(frac=1).reset_index(drop=True)
            # extract true label and it's corresponeding pid for matching
            label = processed_data["label"]
            pid = processed_data["paperID"]
            reorder_idx = processed_data.index
            
            # list of different data field
            part_collection = []
            # select feature wanted to fit to clustering/classification algorithm
            # data part, textual information
            data_combined_emb = extract_embedding(p2v_embedding, pid)
            print(data_combined_emb.shape)
            part_collection.append(data_combined_emb)
            # merge different part of data data together by concatenate it all together
            # remove empty emb (when emb set off)
            part_collection = [part for part in part_collection if len(part)!=0]
            print(len(part_collection))
            if len(part_collection)>1:
                combinedata = np.concatenate(part_collection,axis=1)
            elif len(part_collection)==1:
                if isinstance(part_collection[0], pd.DataFrame):
                    combinedata = part_collection[0].values
                else:
                    combinedata = part_collection[0]
            else:
                print("No data available")
                break
            print(combinedata.shape)
            # using converted feature vector to train classifier
            # using logistic regression
            clf = LogisticRegression()
            LRaccuracy, LRmarcof1 = k_fold_cv(combinedata, label, clf, k=10)
            print("LR Accuracy: ",LRaccuracy)
            print("LR F1: ", LRmarcof1)
            all_LR_accuracy.append(LRaccuracy)
            all_LR_f1.append(LRmarcof1)
            # using SVM with linear kernal
            clf = SVC(kernel='linear')
            svcaccuracy, svcmarcof1 = k_fold_cv(combinedata, label, clf, k=10)
            print("svc Accuracy: ",svcaccuracy)
            print("svc F1: ", svcmarcof1)
            all_svcLinear_accuracy.append(svcaccuracy)
            all_svcLinear_f1.append(svcmarcof1)
# write evaluation result to excel
output = pd.DataFrame({'Author Name':allname,"positive sample size":positive_sample_size,"negative sample size":negative_sample_size, 
                       "svc(linear) accuracy":all_svcLinear_accuracy, "svc(linear) f1": all_svcLinear_f1, 
                       "logistic regression accuracy":all_LR_accuracy, "logistic regression f1": all_LR_f1})

savePath = "../result/"+Dataset+"/binary_local_emb/"
if not os.path.exists(savePath):
    os.makedirs(savePath)
filename = combined_emb+"_threshold="+str(threshold)+".csv"
output.to_csv(savePath+filename, encoding='utf-8',index=False)
print("Done")

For name:  j_read
total sample size before apply threshold:  136
Counter({'0000-0002-5159-1192': 57, '0000-0002-9029-5185': 39, '0000-0002-9697-0962': 31, '0000-0002-4739-9245': 3, '0000-0003-0605-5259': 3, '0000-0003-4316-7006': 1, '0000-0002-0784-0091': 1, '0000-0002-3888-6631': 1})
['0000-0002-9697-0962', '0000-0002-9029-5185', '0000-0002-5159-1192']
(136, 100)
1
(136, 100)
              precision    recall  f1-score   support

           0       0.94      0.52      0.67        31
           1       0.87      0.99      0.93       105

   micro avg       0.88      0.88      0.88       136
   macro avg       0.91      0.75      0.80       136
weighted avg       0.89      0.88      0.87       136

[ 16  15   1 104]
LR Accuracy:  0.8823529411764706
LR F1:  0.7976190476190477
              precision    recall  f1-score   support

           0       0.93      0.84      0.88        31
           1       0.95      0.98      0.97       105

   micro avg       0.95      0.95      0.95       1

/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


              precision    recall  f1-score   support

           0       1.00      0.93      0.97        15
           1       1.00      1.00      1.00       237

   micro avg       1.00      1.00      1.00       252
   macro avg       1.00      0.97      0.98       252
weighted avg       1.00      1.00      1.00       252

[ 14   1   0 237]
svc Accuracy:  0.996031746031746
svc F1:  0.9817059891107078
(252, 100)
1
(252, 100)
              precision    recall  f1-score   support

           0       1.00      0.62      0.77        40
           1       0.93      1.00      0.97       212

   micro avg       0.94      0.94      0.94       252
   macro avg       0.97      0.81      0.87       252
weighted avg       0.94      0.94      0.93       252

[ 25  15   0 212]
LR Accuracy:  0.9404761904761905
LR F1:  0.8675311021552479
              precision    recall  f1-score   support

           0       0.97      0.95      0.96        40
           1       0.99      1.00      0.99       212

 

/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


              precision    recall  f1-score   support

           0       1.00      0.63      0.77        19
           1       0.97      1.00      0.99       233

   micro avg       0.97      0.97      0.97       252
   macro avg       0.99      0.82      0.88       252
weighted avg       0.97      0.97      0.97       252

[ 12   7   0 233]
svc Accuracy:  0.9722222222222222
svc F1:  0.8796971970265294
(252, 100)
1
(252, 100)
              precision    recall  f1-score   support

           0       0.00      0.00      0.00        22
           1       0.91      1.00      0.95       230

   micro avg       0.91      0.91      0.91       252
   macro avg       0.46      0.50      0.48       252
weighted avg       0.83      0.91      0.87       252

[  0  22   0 230]
LR Accuracy:  0.9126984126984127
LR F1:  0.47717842323651455


...

/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


(68, 100)
1
(68, 100)
              precision    recall  f1-score   support

           0       0.83      0.77      0.80        31
           1       0.82      0.86      0.84        37

   micro avg       0.82      0.82      0.82        68
   macro avg       0.82      0.82      0.82        68
weighted avg       0.82      0.82      0.82        68

[24  7  5 32]
LR Accuracy:  0.8235294117647058
LR F1:  0.8210526315789473
              precision    recall  f1-score   support

           0       0.80      0.77      0.79        31
           1       0.82      0.84      0.83        37

   micro avg       0.81      0.81      0.81        68
   macro avg       0.81      0.81      0.81        68
weighted avg       0.81      0.81      0.81        68

[24  7  6 31]
svc Accuracy:  0.8088235294117647
svc F1:  0.806775956284153
(68, 100)
1
(68, 100)
              precision    recall  f1-score   support

           0       0.00      0.00      0.00        10
           1       0.85      1.00      0.92 

/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


(68, 100)
1
(68, 100)
              precision    recall  f1-score   support

           0       0.00      0.00      0.00        11
           1       0.84      1.00      0.91        57

   micro avg       0.84      0.84      0.84        68
   macro avg       0.42      0.50      0.46        68
weighted avg       0.70      0.84      0.76        68

[ 0 11  0 57]
LR Accuracy:  0.8382352941176471
LR F1:  0.45599999999999996
              precision    recall  f1-score   support

           0       0.00      0.00      0.00        11
           1       0.83      0.95      0.89        57

   micro avg       0.79      0.79      0.79        68
   macro avg       0.42      0.47      0.44        68
weighted avg       0.70      0.79      0.74        68

[ 0 11  3 54]
svc Accuracy:  0.7941176470588235
svc F1:  0.4426229508196722
Done


/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


In [18]:
# accuracy
from statistics import mean 
cleaned_svcLinear_accuracy = [x for x in all_svcLinear_accuracy if isinstance(x, float)]
cleaned_lr_accuracy = [x for x in all_LR_accuracy if isinstance(x, float)]
print(len(cleaned_svcLinear_accuracy))
print(len(cleaned_lr_accuracy))
print(mean(cleaned_svcLinear_accuracy))
print(mean(cleaned_lr_accuracy))

3227
3227
0.9528755428623408
0.9154026206002153


In [19]:
# f1
from statistics import mean 
# remove string from result
cleaned_svcLinear_f1 = [x for x in all_svcLinear_f1 if isinstance(x, float)]
cleaned_lr_f1 = [x for x in all_LR_f1 if isinstance(x, float)]
print(len(cleaned_svcLinear_f1))
print(len(cleaned_lr_f1))
print(mean(cleaned_svcLinear_f1))
print(mean(cleaned_lr_f1))

3227
3227
0.8042025519598761
0.6561471404975902


In [ ]:
%reset

In [ ]:
%who